#  Dependecies

In [1]:
!pip3 install -U ncps pytorch-lightning ucimlrepo

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.3/60.3 kB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.0/823.0 kB 24.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 29.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 22.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 16.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 10.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 44.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 

In [2]:
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd
import numpy as np
import torch.nn as nn
from ncps.wirings import AutoNCP
from ncps.torch import LTC, CfC
import pytorch_lightning as pl
import torch
import torch.utils.data as data
from torchvision.datasets import MNIST
import torchvision.transforms as transforms



# Gesture dataset

In [3]:
# Download ozone dataset
!wget https://archive.ics.uci.edu/static/public/302/gesture+phase+segmentation.zip


--2025-03-26 17:18:31--  https://archive.ics.uci.edu/static/public/302/gesture+phase+segmentation.zip
Resolving archive.ics.uci.edu (archive.ics.uci.edu)... 128.195.10.252
Connecting to archive.ics.uci.edu (archive.ics.uci.edu)|128.195.10.252|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified
Saving to: ‘gesture+phase+segmentation.zip’

gesture+phase+segme     [ <=>                ]   1.85M  9.98MB/s    in 0.2s    

2025-03-26 17:18:31 (9.98 MB/s) - ‘gesture+phase+segmentation.zip’ saved [1943494]



In [4]:
!unzip gesture+phase+segmentation.zip

Archive:  gesture+phase+segmentation.zip
  inflating: a1_va3.csv              
  inflating: a2_raw.csv              
  inflating: a2_va3.csv              
  inflating: a3_raw.csv              
  inflating: a3_va3.csv              
  inflating: b1_raw.csv              
  inflating: b1_va3.csv              
  inflating: b3_raw.csv              
  inflating: b3_va3.csv              
  inflating: c1_raw.csv              
  inflating: c1_va3.csv              
  inflating: c3_raw.csv              
  inflating: c3_va3.csv              
  inflating: data_description.txt    
  inflating: a1_raw.csv              


## Data description

1. Title: Gesture Phase Segmentation

2. Sources:

     (a) Creators:
		Renata Cristina Barros Madeo (Madeo, R. C. B.)
		Priscilla Koch Wagner (Wagner, P. K.)
            	Sarajane Marques Peres (Peres, S. M.)
        	{renata.si, priscilla.wagner, sarajane} at usp.br
                http://each.uspnet.usp.br/sarajane/

     (b) Donor:
		University of Sao Paulo
		School of Art, Sciences and Humanities
		Sao Paulo, SP, Brazil
		http://www5.usp.br/en/

     (c) Date: June, 2014


3. Past Usage:

   1.  Madeo, R. C. B. ; Lima, C. A. M. ; PERES, S. M. . Gesture Unit Segmentation using Support Vector Machines: Segmenting
       Gestures from Rest Positions. In: Symposium on Applied Computing (SAC), 2013, Coimbra. Proceedings of the 28th Annual
       ACM Symposium on Applied Computing (SAC), 2013. p. 46-52.
       * In this paper, the videos A1 and A2 were studied.

   2.  Wagner, P. K. ; PERES, S. M. ; Madeo, R. C. B. ; Lima, C. A. M. ; Freitas, F. A. . Gesture Unit Segmentation Using
       Spatial-Temporal Information and Machine Learning. In: 27th Florida Artificial Intelligence Research Society Conference
       (FLAIRS), 2014, Pensacola Beach. Proceedings of the 27th Florida Artificial Intelligence Research Society Conference
       (FLAIRS). Palo Alto : The AAAI Press, 2014. p. 101-106.
       * In this paper, the videos A1, A2, A3, B1, B3, C1 and C3 were studied.

   3.  Madeo, R. C. B.. Support Vector Machines and Gesture Analysis: incorporating temporal aspects  (in Portuguese). Master
       Thesis - Universidade de Sao Paulo, Sao Paulo Researcher Foundation. 2013.
       * In this document, the videos named B1 and B3 in the document correspond to videos C1 and C3 in this dataset. Only
       five videos were explored in this document: A1, A2, A3, C1 and C3.

   4.  Wagner, P. K. ; Madeo, R. C. B. ; PERES, S. M. ; Lima, C. A. M.. Segmenta�ao de Unidades Gestuais com Multilayer
       Perceptrons (in Portuguese). In: Encontro Nacional de Inteligencia Artificial e Computacional (ENIAC), 2013, Fortaleza.
       Anais do X Encontro Nacional de Inteligencia Artificial e Computacional (ENIAC), 2013.
       * In this paper, the videos A1, A2 and A3 were studied.


4. Relevant Information:


       Gesture Phase Segmentation consists in a temporal segmentation of gestures, performed by gesture researchers in
       order to preprocess videos for further analysis. The description of gesture phase segmentation problem may be found
       in MADEO et al. (2013a) and MADEO et al. (2013b).
---
       The dataset is composed by seven videos recorded using Microsoft Kinect sensor. Three different users were asked
       to read three comic strips and to tell the stories in front of the sensor. Using Microsoft Kinect, we have obtained:
       (a) a image of each frame, identified by a timestamp; (b) a text file containing positions (coordinates x, y, z) of
       six articulation points -- left hand, right hand, left wrist, right wrist, head and spine, with each line in the file
       corresponding to a frame and identified by a timestamp. The images enabled a manual segmentation of each file by a
       specialist, providing a ground truth for classification.

   ---
       The dataset is organized in 14 files: 7 raw files and 7 processed files, one for each video which compose the dataset.
       The name of the file refers to each video: the letter corresponds to the user (A, B, C) and the number corresponds to
       the story (1, 2, 3). The raw files contain the information obtained from Microsoft Kinect, described above. The processed
       file contains vectorial and scalar velocity and acceleration of left hand, right hand, left wrist, and right wrist. These
       measures were obtained after normalizing positions of hand and wrists considering the position of head and spine, and
       using a displacement equal to 3 in order to measure velocity, as described in MADEO et al. (2013c).


5. Number of Instances:

	A1 - 1747 frames
	A2 - 1264 frames
	A3 - 1834 frames
	B1 - 1073 frames
	B3 - 1423 frames
	C1 - 1111 frames
	C3 - 1448 frames


6. Number of Attributes:

	Raw files (*_raw.csv): 	      18 numeric attributes (double), a timestamp (integer) and a class attribute (nominal).

	Processed files (*_va3.csv):  32 numeric attributes (double) and a class attribute (nominal).

    A feature vector with up to 51 numeric attributes can be generated with the two files mentioned above.


7. Attribute Information:

   Raw files:

   1. lhx - Position of left hand (x coordinate)
   2. lhy - Position of left hand (y coordinate)
   3. lhz - Position of left hand (z coordinate)
   4. rhx - Position of right hand (x coordinate)
   5. rhy - Position of right hand (y coordinate)
   6. rhz - Position of right hand (z coordinate)
   7. hx - Position of head (x coordinate)
   8. hy - Position of head  (y coordinate)
   9. hz - Position of head  (z coordinate)
   10. sx - Position of spine (x coordinate)
   11. sy - Position of spine (y coordinate)
   12. sz - Position of spine (z coordinate)
   13. lwx - Position of left wrist (x coordinate)
   14. lwy - Position of left wrist (y coordinate)
   15. lwz - Position of left wrist (z coordinate)
   16. rwx - Position of right wrist (x coordinate)
   17. rwy - Position of right wrist (y coordinate)
   18. rwz - Position of right wrist (z coordinate)
   19. timestamp -
   20. phase:
		-- Rest
		-- Preparation
		-- Stroke
		-- Hold
		-- Retraction

   Processed files:

   1. Vectorial velocity of left hand (x coordinate)
   2. Vectorial velocity of left hand (y coordinate)
   3. Vectorial velocity of left hand (z coordinate)
   4. Vectorial velocity of right hand (x coordinate)
   5. Vectorial velocity of right hand (y coordinate)
   6. Vectorial velocity of right hand (z coordinate)
   7. Vectorial velocity of left wrist (x coordinate)
   8. Vectorial velocity of left wrist (y coordinate)
   9. Vectorial velocity of left wrist (z coordinate)
   10. Vectorial velocity of right wrist (x coordinate)
   11. Vectorial velocity of right wrist (y coordinate)
   12. Vectorial velocity of right wrist (z coordinate)
   13. Vectorial acceleration of left hand (x coordinate)
   14. Vectorial acceleration of left hand (y coordinate)
   15. Vectorial acceleration of left hand (z coordinate)
   16. Vectorial acceleration of right hand (x coordinate)
   17. Vectorial acceleration of right hand (y coordinate)
   18. Vectorial acceleration of right hand (z coordinate)
   19. Vectorial acceleration of left wrist (x coordinate)
   20. Vectorial acceleration of left wrist (y coordinate)
   21. Vectorial acceleration of left wrist (z coordinate)
   22. Vectorial acceleration of right wrist (x coordinate)
   23. Vectorial acceleration of right wrist (y coordinate)
   24. Vectorial acceleration of right wrist (z coordinate)
   25. Scalar velocity of left hand
   26. Scalar velocity of right hand
   27. Scalar velocity of left wrist
   28. Scalar velocity of right wrist
   29. Scalar velocity of left hand
   30. Scalar velocity of right hand
   31. Scalar velocity of left wrist
   32. Scalar velocity of right wrist
   33. phase:
		-- D (rest position, from portuguese "descanso")
		-- P (preparation)
		-- S (stroke)
		-- H (hold)
		-- R (retraction)


8. Missing Attribute Values: None

9. Extra information:

       Gesture phase segmentation is a task with several inherent difficulties. First, it is a subjective task, since there
       is no clear point where a phase begins. Thus, different specialists may provide different segmentations for the same
       video. Also, some phases may present similar patterns, such as rest position and hold, where the hands remain paused.
       Finally, gesture phase segmentation has open issues among researchers, such as if the phases should be segmented
       separatedly for each hand or if meaningless gesture -- such as touching the glasses while speaking -- may be considered
       for gesture phase segmentation.

       Also, it is important to consider that the gesticulation behavior may influence the performance of a classifier built
       for gesture segmentation. Thus, it is important to highlight that videos A1 and A2 were recorded in the same session,
       while video A3 was recorded in a different session, which may yield different gesticulation behaviour.


10. References:

       Madeo, R. C. B. ; Lima, C. A. M. ; PERES, S. M. . Gesture Unit Segmentation using Support Vector Machines: Segmenting
       Gestures from Rest Positions. In: Symposium on Applied Computing (SAC), 2013, Coimbra. Proceedings of the 28th Annual
       ACM Symposium on Applied Computing (SAC), 2013a. p. 46-52.       

       Madeo, R. C. B. ; Wagner, P. K. ; PERES, S. M.. A Review of Temporal Aspects of Hand Gesture Analysis Applied to
       Discourse Analysis and Natural Conversation. International Journal of Computer Science and Information Technology
       (Print), v. 5, p. 1-20, 2013b.

       Madeo, R. C. B.. Support Vector Machines and Gesture Analysis: incorporating temporal aspects (in Portuguese). Master
       Thesis - Universidade de Sao Paulo, Sao Paulo Researcher Foundation. 2013c.

## Data preprocessing

The input features at each time step are comprised of 32 data points recorded from a motion detection sensor.

    We will use only *va3.csv files, because 32 features are only inside them.

The output, at each time step, represents one of the five possible hand gestures: rest position, preparation, stroke, hold, and retraction.

    phase:
    -- D (rest position, from portuguese "descanso")
    -- P (preparation)
    -- S (stroke)
    -- H (hold)
    -- R (retraction)

The objective is to train a classifier to detect hand gestures from the motion data.  

We cut each of the seven recordings into overlapping sub-sequences of exactly 32 time steps. We randomly separated all sub-sequences into non-overlapping training (75%), validation (10%), and test (15%) sets. Input features were normalized to have zero mean and unit standard deviation. We used the categorical classification accuracy as the performance metric.  

In [5]:
a1_va3 = pd.read_csv("a1_va3.csv")
a2_va3 = pd.read_csv("a2_va3.csv")
a3_va3 = pd.read_csv("a3_va3.csv")
b1_va3 = pd.read_csv("b1_va3.csv")
b3_va3 = pd.read_csv("b3_va3.csv")
c1_va3 = pd.read_csv("c1_va3.csv")
c3_va3 = pd.read_csv("c3_va3.csv")

In [6]:
df = pd.concat([a1_va3, a2_va3, a3_va3, b1_va3, b3_va3, c1_va3, c3_va3], ignore_index=True)

In [7]:
target_class_mapping = {"D": 0, "P": 1, "S": 2, "H": 3, "R": 4}
# Apply the mapping to the Phase column
df['Phase'] = df['Phase'].replace(target_class_mapping)

<ipython-input-7-fdcbcf412bda>:3: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df['Phase'] = df['Phase'].replace(target_class_mapping)


In [8]:
df

1         2         3         4         5         6         7  \
0    -0.005009 -0.000964  0.000573  0.008623  0.005667  0.001302 -0.000631   
1     0.004905  0.001209 -0.000649  0.004737  0.003166  0.000819 -0.000572   
2    -0.002393 -0.000216  0.000136  0.003028  0.001212  0.000336 -0.000449   
3    -0.001394 -0.000242  0.000056  0.001182  0.000575  0.000225 -0.000479   
4    -0.000156 -0.000004  0.000023  0.001585  0.000630  0.000094 -0.000303   
...        ...       ...       ...       ...       ...       ...       ...   
9868 -0.003709 -0.006168  0.000786 -0.000155  0.001088 -0.000144 -0.003815   
9869 -0.000727  0.001536 -0.000211  0.000700 -0.000975  0.000067 -0.001147   
9870  0.003074  0.007870 -0.000962  0.000526 -0.000779  0.000090  0.002786   
9871  0.003297  0.008467 -0.001035  0.000578 -0.000740  0.000101  0.002947   
9872  0.000204 -0.000040  0.000058  0.000586 -0.000619  0.000087  0.000229   

             8         9        10  ...            24        25        26  \
0     0.000130 -0.000048  0.007762  ...  1.880800e-04  0.005133  0.010400   
1    -0.000015  0.000023  0.002706  ... -7.500000e-07  0.005093  0.005756   
2     0.000017  0.000047  0.002868  ... -3.920000e-05  0.002406  0.003279   
3    -0.000050  0.000104  0.001171  ... -3.184000e-05  0.001416  0.001334   
4     0.000097  0.000065  0.001579  ... -2.015000e-05  0.000158  0.001709   
...        ...       ...       ...  ...           ...       ...       ...   
9868 -0.004658  0.000656  0.000060  ... -9.400000e-07  0.007240  0.001109   
9869  0.000177  0.000008  0.000423  ...  1.234000e-05  0.001712  0.001202   
9870  0.005035 -0.000606  0.000413  ...  2.327000e-05  0.008504  0.000944   
9871  0.005385 -0.000652  0.000580  ...  1.541000e-05  0.009145  0.000944   
9872  0.000003  0.000061  0.000644  ...  3.200000e-07  0.000216  0.000857   

            27        28        29        30        31        32  Phase  
0     0.000646  0.007871  0.004631  0.000963  0.000092  0.000438      0  
1     0.000573  0.003459  0.000730  0.000332  0.000012  0.000433      0  
2     0.000452  0.003261  0.002412  0.000852  0.000042  0.000202      0  
3     0.000493  0.001358  0.000313  0.000611  0.000029  0.000596      0  
4     0.000325  0.001713  0.000203  0.000069  0.000038  0.000069      0  
...        ...       ...       ...       ...       ...       ...    ...  
9868  0.006056  0.000173  0.001976  0.000137  0.001575  0.000051      0  
9869  0.001160  0.000515  0.002600  0.000701  0.001738  0.000124      0  
9870  0.005786  0.000431  0.002007  0.000071  0.001697  0.000112      0  
9871  0.006173  0.000699  0.000229  0.000023  0.000139  0.000113      0  
9872  0.000237  0.000808  0.002763  0.000037  0.001840  0.000036      0  

[9873 rows x 33 columns]

In [9]:
X_np = df.drop(["Phase"], axis=1).to_numpy()
y_np = df["Phase"].to_numpy(dtype=np.int64)

In [10]:
print(f"shape of X: {X_np.shape}")
print(f"shape of y: {y_np.shape}")


shape of X: (9873, 32)
shape of y: (9873,)


In [11]:
print(f"dtype of X: {X_np.dtype}")
print(f"dtype of y: {y_np.dtype}")

dtype of X: float64
dtype of y: int64


Original authors standardize all data column-wise using all data, including target value, not only the train set

In [12]:
X_np -= X_np.mean(axis=0)
X_np /= X_np.std(axis=0)

In [13]:
def cut_in_sequences(x,y,seq_len,inc=1):

    sequences_x = []
    sequences_y = []

    for s in range(0,x.shape[0] - seq_len,inc):
        start = s
        end = start+seq_len
        sequences_x.append(x[start:end])
        sequences_y.append(y[start:end])

    return np.stack(sequences_x,axis=0), np.stack(sequences_y,axis=0)

# producing half-overlapping sequences of 32 timesteps
X_sequences, y_sequences = cut_in_sequences(X_np,y_np,seq_len=32,inc=16)

print(f"shape of X_sequences: {X_sequences.shape}")
print(f"shape of y_sequences: {y_sequences.shape}")


shape of X_sequences: (616, 32, 32)
shape of y_sequences: (616, 32)


In [14]:
total_seqs = X_sequences.shape[0]
print("Total number of training sequences: {}".format(total_seqs))

Total number of training sequences: 616


In [15]:
permutation = np.random.RandomState(23489).permutation(total_seqs)

In [16]:
# they used those amount of sequences for validation and test sets
valid_size = int(0.1*total_seqs)
test_size = int(0.15*total_seqs)
train_size = total_seqs - valid_size - test_size
print(f"Train sequences:{train_size}, validation sequences: {valid_size}, test sequences: {test_size}")

Train sequences:463, validation sequences: 61, test sequences: 92


In [17]:
# sequences for train, validation and test in numpy
X_val = X_sequences[permutation[:valid_size],:]
y_val = y_sequences[permutation[:valid_size],:]
X_test = X_sequences[permutation[valid_size:valid_size+test_size],:]
y_test = y_sequences[permutation[valid_size:valid_size+test_size],:]
X_train = X_sequences[permutation[valid_size+test_size:],:]
y_train = y_sequences[permutation[valid_size+test_size:],:]

In [18]:
# convert to tensors
X_train = torch.tensor(X_train, dtype=torch.float32)
y_train = torch.tensor(y_train, dtype=torch.long)
X_test =  torch.tensor(X_test , dtype=torch.float32)
y_test =  torch.tensor(y_test , dtype=torch.long)
X_val =   torch.tensor(X_val  , dtype=torch.float32)
y_val =   torch.tensor(y_val  , dtype=torch.long)

In [19]:
# move to gpu if possible
if torch.cuda.is_available():
    device = torch.device('cuda')
    print("device selected: cuda")
else:
    device = torch.device('cpu')
    print("device selected: cpu")

X_train = X_train.to(device)
y_train = y_train.to(device)

X_test = X_test.to(device)
y_test = y_test.to(device)

X_val = X_val.to(device)
y_val = y_val.to(device)


device selected: cuda


In [20]:
from torch.utils.data import TensorDataset, DataLoader

train_dataset = TensorDataset(X_train, y_train)
val_dataset = TensorDataset(X_val, y_val)
test_dataset = TensorDataset(X_test, y_test)

train_loader = DataLoader(train_dataset, batch_size=32, shuffle=False) # Not to shuffle for reproducibility
val_loader = DataLoader(val_dataset, batch_size=32, shuffle=False)  # No need to shuffle validation
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)  # No need to shuffle test


In [21]:
import torch
import torch.nn as nn
import torch.optim as optim
import pytorch_lightning as pl
import numpy as np
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

class SequenceLearner(pl.LightningModule):
    def __init__(self, model, lr=0.001, num_classes = 5):
        """
        :param model: The PyTorch model to train.
        :param lr: Learning rate.
        """
        super().__init__()
        self.model = model
        self.lr = lr
        self.num_classes = num_classes

        # Use CrossEntropyLoss for multiclass classification
        self.loss_fn = nn.CrossEntropyLoss()

        # Initialize empty lists to store predictions and labels during validation/testing
        self.preds_validation = []
        self.labels_validation = []
        self.preds_test = []
        self.labels_test = []

    def forward(self, x):
        return self.model(x)

    def compute_loss(self, logits, y):
        """ Compute cross-entropy loss. """
        return self.loss_fn(logits.view(-1,self.num_classes), y.view(-1))

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits, _ = self.model(x)
        loss = self.compute_loss(logits, y)

        # Log the loss
        self.log("train_loss", loss, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits, _ = self.model(x)
        loss = self.compute_loss(logits, y)

        # Store predictions and labels for metrics
        preds = torch.argmax(logits, dim=2)
        # assert False, f"logits_shape: {logits.shape}, preds_shape: {preds.shape}, y_shape: {y.shape}"
        # Store predictions and labels for metrics
        self.preds_validation.extend(list(preds.cpu().detach().numpy().reshape(-1)))
        self.labels_validation.extend(list(y.cpu().detach().numpy().reshape(-1)))

        # Log the loss
        self.log("val_loss", loss, prog_bar=True)
        return loss

    def on_validation_epoch_end(self):
        """ Calculate metrics at the end of validation epoch. """
        preds = np.array(self.preds_validation)
        labels = np.array(self.labels_validation)

        # Compute metrics
        accuracy = accuracy_score(labels, preds)
        precision = precision_score(labels, preds, average='macro')
        recall = recall_score(labels, preds, average='macro')
        f1 = f1_score(labels, preds, average='macro')

        # Log metrics
        self.log("val_accuracy", accuracy, prog_bar=True)
        self.log("val_precision", precision, prog_bar=True)
        self.log("val_recall", recall, prog_bar=True)
        self.log("val_f1", f1, prog_bar=True)

        # Clear lists for next epoch
        self.preds_validation.clear()
        self.labels_validation.clear()

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits,_ = self.model(x)
        loss = self.compute_loss(logits, y)

        # Store predictions and labels
        preds = torch.argmax(logits, dim=2)
        self.preds_test.extend(list(preds.cpu().detach().numpy().reshape(-1)))
        self.labels_test.extend(list(y.cpu().detach().numpy().reshape(-1)))

        return loss

    def configure_optimizers(self):
        return optim.Adam(self.model.parameters(), lr=self.lr)

In [22]:
# Adjust LTC model parameters
in_features = X_np.shape[1]  # Number of features in the dataset
out_features = 5  # Last dimension size for the input of the CrossEntropyLoss (we have 5 classes, so it must be 5)
RNN_state_size = 32  # number of hidden units (BPTT length)


Here we can finally create a LTCCell and make use of the predefined sparse wiring structures of the keras-ncp package. For simplicity we will just define a fully-connected RNN

In [23]:
wiring = AutoNCP(units=RNN_state_size, output_size=out_features, sparsity_level=0.5)
ltc_model = LTC(input_size=in_features, units=wiring).to(device)
cfc_model = CfC(input_size=in_features, units=wiring).to(device)

model = SequenceLearner(ltc_model, lr=0.01).to(device)
trainer = pl.Trainer(
    logger=pl.loggers.CSVLogger("log"),
    max_epochs=200,
    gradient_clip_val=1,  # Clip gradient to stabilize training
)

INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


In [24]:
trainer.fit(model, train_loader, val_loader)

INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name    | Type             | Params | Mode 
-----------------------------------------------------
0 | model   | LTC              | 10.4 K | train
1 | loss_fn | CrossEntropyLoss | 0      | train
-----------------------------------------------------
8.4 K     Trainable params
2.0 K     Non-trainable params
10.4 K    Total params
0.042     Total estimated model params size (MB)
5         Modules in train mode
0         Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/pytorch_lightning/loops/fit_loop.py:310: The number of training batches (15) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.


Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=200` reached.


In [25]:
model.preds_test = []
model.labels_test = []
trainer.test(model, test_loader)

INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

[{}]

In [26]:
predictions = np.array(model.preds_test)
ground_truth = np.array(model.labels_test)

In [52]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=ground_truth, mode='lines', name='Ground Truth'))
fig.add_trace(go.Scatter(y=predictions, mode='lines', name='Predictions'))
fig.update_layout(title="Gesture Phase Segmentation: LTC model, 200 epochs", template="simple_white")
fig.update_yaxes(title="Gesture Class", showgrid=True, dtick=1)
fig.show()

In [31]:
from sklearn.metrics import f1_score, precision_score, recall_score, accuracy_score

# Assuming 'predictions' and 'labels' are your numpy arrays
f1 = f1_score(ground_truth, predictions,average="macro")
precision = precision_score(ground_truth, predictions,average="macro")
recall = recall_score(ground_truth, predictions,average="macro")
accuracy = accuracy_score(ground_truth, predictions)

print(f"\n✅ Test Metrics:")
print(f"{'F1 Score':<10}: {round(f1,3)}")
print(f"{'Precision':<10}: {round(precision,3)}")
print(f"{'Recall':<10}: {round(recall,3)}")
print(f"{'Accuracy':<10}: {round(accuracy,3)}")


✅ Test Metrics:
F1 Score  : 0.583
Precision : 0.592
Recall    : 0.582
Accuracy  : 0.626


In [40]:
wiring = AutoNCP(units=RNN_state_size, output_size=out_features, sparsity_level=0.5)
ltc_model = LTC(input_size=in_features, units=wiring).to(device)
cfc_model = CfC(input_size=in_features, units=wiring).to(device)

model = SequenceLearner(cfc_model, lr=0.01).to(device)
trainer = pl.Trainer(
    logger=pl.loggers.CSVLogger("log"),
    max_epochs=200,
    gradient_clip_val=1,  # Clip gradient to stabilize training
)
trainer.fit(model, train_loader, val_loader)


INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name    | Type             | Params | Mode 
-----------------------------------------------------
0 | model   | CfC              | 6.0 K  | train
1 | loss_fn | CrossEntropyLoss | 0      | train
-----------------------------------------------------
4.8 K     Trainable params
1.2 K     Non-trainable params
6.0 K     Total params
0.024     Total estimated model params size (MB)
25        Modules in train mode
0         Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/pytorch_lightning/loops/fit_loop.py:310: PossibleUserWarning:

The number of training batches (15) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.



Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=200` reached.


In [43]:
model.preds_test = []
model.labels_test = []
trainer.test(model, test_loader)
predictions_cfc = np.array(model.preds_test)
ground_truth_cfc = np.array(model.labels_test)


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

In [53]:

fig = go.Figure()
fig.add_trace(go.Scatter(y=ground_truth_cfc, mode='lines', name='Ground Truth'))
fig.add_trace(go.Scatter(y=predictions_cfc, mode='lines', name='Predictions'))
fig.update_layout(title="Gesture Phase Segmentation: CfC model, 200 epochs", template="simple_white")
fig.update_yaxes(title="Gesture Class", showgrid=True, dtick=1)
fig.show()

In [45]:
metrics_cfc = pd.read_csv("/content/log/lightning_logs/version_1/metrics.csv")
metrics_ltc = pd.read_csv("/content/log/lightning_logs/version_0/metrics.csv")
df_val_metrics_cfc = metrics_cfc.drop("train_loss", axis=1).dropna()
df_val_metrics_ltc = metrics_ltc.drop("train_loss", axis=1).dropna()

In [50]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_val_metrics_ltc["epoch"], y=df_val_metrics_ltc["val_accuracy"], mode='lines', name='LTC'))
fig.add_trace(go.Scatter(x=df_val_metrics_cfc["epoch"], y=df_val_metrics_cfc["val_accuracy"], mode='lines', name='CfC'))
fig.add_trace(go.Scatter(x=[0,200], y=[0.6955, 0.6955], mode='lines', name='Best result of the article', line=dict(dash="dash")))
fig.update_layout(title="Gesture Phase Segmentation: validation accuracy", template="simple_white")
fig.update_yaxes(title="", showgrid=True, range = [0,1] , dtick=0.1)
fig.update_xaxes(title="Epoch", showgrid=True, range=[0,201], dtick=20)
fig.show()
